In [1]:
!pip install umap-learn

In [27]:
import plotly.graph_objects as go
import numpy as np
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import os
from sklearn.metrics import precision_recall_curve
from collections import Counter
# from tqdm import tqdm_notebook as tqdm
# tqdm().pandas()
import json
import pickle
from keras.callbacks import ModelCheckpoint
from keras.callbacks import EarlyStopping
from keras.models import load_model
from sklearn.model_selection import StratifiedKFold
from keras.models import load_model
from sklearn.metrics import log_loss
from keras import regularizers
from keras.models import Sequential
from keras.layers import LSTM
from keras.layers import Dense
from keras.layers import Activation
from keras.layers import Dropout
from keras.layers import Flatten
import tensorflow as tf
import random
from matplotlib import pyplot as plt
import seaborn as sns
import os
import umap
from imblearn.over_sampling import SMOTE
from sklearn.cluster import KMeans
from keras import backend as K
from sklearn.manifold import TSNE
from IPython.core.display import display, HTML
from sklearn.preprocessing import StandardScaler, MinMaxScaler
display(HTML("<style>.container { width:80% !important; }</style>"))
from plotly.offline import init_notebook_mode, iplot
from sklearn.decomposition import PCA
import warnings
warnings.filterwarnings('ignore')

# Read input

In [3]:
df = pd.read_csv("df_full.csv")
df.shape

(931462, 12)

In [4]:
df.head()

compute                   timespan  arrTemperature0  arrTemperature1  \
0  compute-1-1  2019-06-09 00:00:00+00:00               73               59   
1  compute-1-1  2019-06-09 00:05:00+00:00               73               59   
2  compute-1-1  2019-06-09 00:10:00+00:00               73               59   
3  compute-1-1  2019-06-09 00:15:00+00:00               73               59   
4  compute-1-1  2019-06-09 00:20:00+00:00               73               59   

   arrTemperature2  arrCPU_load0  arrMemory_usage0  arrFans_health0  \
0               21      5.387361          8.585885             9170   
1               21      5.408750          8.590575             9170   
2               21      5.363472          8.578069             9170   
3               21      5.342361          8.600996             8890   
4               21      5.288056          8.608813             8890   

   arrFans_health1  arrFans_health2  arrFans_health3  arrPower_usage0  
0             9170             9310             9310         105.3125  
1             9310             8960             9310         105.3125  
2             9310             9100             9170         105.3125  
3             8890             8960             8960         105.3125  
4             8750             8750             8750         105.0000

In [5]:
some_computers = list(pd.DataFrame(df.compute.value_counts()).head(3).index)

In [6]:
df = df[df.compute.isin(some_computers)]
df.shape

(6012, 12)

# Normalization

In [7]:
data = df.drop(columns=["compute", "timespan"])

In [8]:
min_values = [3] * 3 + [0] + [0] + [1050]*4 + [0]
max_values = [98] * 3 + [10] + [99] + [17850]*4 + [200]

min_max_df = pd.DataFrame(data = [min_values, max_values], columns= data.columns)
min_max_df

arrTemperature0  arrTemperature1  arrTemperature2  arrCPU_load0  \
0                3                3                3             0   
1               98               98               98            10   

   arrMemory_usage0  arrFans_health0  arrFans_health1  arrFans_health2  \
0                 0             1050             1050             1050   
1                99            17850            17850            17850   

   arrFans_health3  arrPower_usage0  
0             1050                0  
1            17850              200

In [9]:
data = pd.concat([data, min_max_df],0).reset_index(drop=True)

In [10]:
scaler = MinMaxScaler()
scaler.fit(data)

MinMaxScaler(copy=True, feature_range=(0, 1))

In [11]:
data

arrTemperature0  arrTemperature1  arrTemperature2  arrCPU_load0  \
0                  40               32               16      0.000556   
1                  39               32               16      0.000694   
2                  40               32               16      0.000833   
3                  39               31               16      0.000694   
4                  40               32               16      0.000694   
...               ...              ...              ...           ...   
6009               64               50               14      0.469167   
6010               65               49               13      0.470278   
6011               64               48               14      0.466806   
6012                3                3                3      0.000000   
6013               98               98               98     10.000000   

      arrMemory_usage0  arrFans_health0  arrFans_health1  arrFans_health2  \
0            11.064156             8750             8050             8680   
1            11.063635             9100             8750             8960   
2            11.063635             9100             8120             8750   
3            11.064156             8750             8260             8330   
4            11.062592             8890             8750             8960   
...                ...              ...              ...              ...   
6009         51.642975            11550            11480            11480   
6010         51.619526            11550            11480            11550   
6011         51.617963            11550            11550            11550   
6012          0.000000             1050             1050             1050   
6013         99.000000            17850            17850            17850   

      arrFans_health3  arrPower_usage0  
0                8050          42.1875  
1                8680          42.1875  
2                8750          41.8750  
3                8260          43.1250  
4                8680          42.1875  
...               ...              ...  
6009            11480          95.9375  
6010            11480          97.1875  
6011            11480         101.8750  
6012             1050           0.0000  
6013            17850         200.0000  

[6014 rows x 10 columns]

In [12]:
scaled_data = scaler.transform(data.iloc[:-2,:])
print(scaled_data.shape)
scaled_data

(6012, 10)


array([[0.38947368, 0.30526316, 0.13684211, ..., 0.45416667, 0.41666667,
        0.2109375 ],
       [0.37894737, 0.30526316, 0.13684211, ..., 0.47083333, 0.45416667,
        0.2109375 ],
       [0.38947368, 0.30526316, 0.13684211, ..., 0.45833333, 0.45833333,
        0.209375  ],
       ...,
       [0.64210526, 0.49473684, 0.11578947, ..., 0.62083333, 0.62083333,
        0.4796875 ],
       [0.65263158, 0.48421053, 0.10526316, ..., 0.625     , 0.62083333,
        0.4859375 ],
       [0.64210526, 0.47368421, 0.11578947, ..., 0.625     , 0.62083333,
        0.509375  ]])

# Clustering

In [13]:
X=scaled_data

In [14]:
## Use k-means++ 
distortions = []
max_num_clusters = 20
for i in range(1, max_num_clusters):
    km = KMeans(
        n_clusters=i, init='k-means++',
        n_init=10, max_iter=300,
        tol=1e-04, random_state=0, n_jobs= -1
    )
    km.fit(X)
    distortions.append(km.inertia_)
    print(f"Done step {i}/{max_num_clusters}")

Done step 1/20
Done step 2/20
Done step 3/20
Done step 4/20
Done step 5/20
Done step 6/20
Done step 7/20
Done step 8/20
Done step 9/20
Done step 10/20
Done step 11/20
Done step 12/20
Done step 13/20
Done step 14/20
Done step 15/20
Done step 16/20
Done step 17/20
Done step 18/20
Done step 19/20


In [15]:
x = list(range(1, max_num_clusters))

fig = go.Figure(data=go.Scatter(x=x, y=distortions))
fig.show()

In [16]:
num_clusters= 5
km = KMeans(
    n_clusters=num_clusters, init='k-means++',
    n_init=10, max_iter=300,
    tol=1e-04, random_state=0, n_jobs= -1
)
km.fit(X)
print(f"Done K-means++!")

Done K-means++!


In [17]:
label = pd.DataFrame(km.labels_, columns= ["label"])

# Dimension reduction

In [33]:
### https://www.kaggle.com/kevinarvai/genomic-visualization-via-dimensionality-reduction
def reduce_dim(X, algorithm='PCA', n_components=3, df =df):
    """
    param algorithm: The type of dimensionality reduction to perform. 
        One of {PCA, UMAP, TSNE}
    :returns: The transformed X[m, n] array - reduced to X[m, n_components] by `algorithm`
    """
    
    if algorithm == 'PCA':
        pca = PCA(n_components=n_components).fit(X)
        X_red = pca.transform(X)
        df_red = pd.DataFrame(X_red, 
                              index=df.index, 
                              columns=['component1', 'component2', 'component3'])
    elif algorithm == 'TSNE':
        # TSNE, Barnes-Hut have dim <= 3
        if n_components > 3:
            print('The Barnes-Hut method requires the dimensionaility to be <= 3')
            return None
        else:
            X_red = TSNE(n_components=n_components, n_jobs=-1).fit_transform(X)
            df_red = pd.DataFrame(X_red, 
                                  index=df.index, 
                                  columns=['component1', 'component2', 'component3'])
    elif algorithm == 'UMAP':
        umap_ = umap.UMAP(n_components=n_components).fit(X)
        X_red = umap_.transform(X)
        df_red = pd.DataFrame(X_red, 
                              index=df.index, 
                              columns=['component1', 'component2', 'component3'])
    else:
        return None
    
    return df_red.reset_index(drop=True)


def generate_figure_image(groups, layout):
    data = []

    for idx, val in groups:
        if idx == 'me':
            scatter = go.Scatter3d(
            name=idx,
            x=val.loc[:, 'component1'],
            y=val.loc[:, 'component2'],
            z=val.loc[:, 'component3'],
            text=[idx for _ in range(val.loc[:, 'component1'].shape[0])],
            textposition='middle right',
            mode='markers',
            marker=dict(
                size=12,
                symbol='diamond'
                )
            )
        else:
            scatter = go.Scatter3d(
                name=idx,
                x=val.loc[:, 'component1'],
                y=val.loc[:, 'component2'],
                z=val.loc[:, 'component3'],
                text=[idx for _ in range(val.loc[:, 'component1'].shape[0])],
                textposition='middle right',
                mode='markers',
                marker=dict(
                    size=4,
                    symbol='circle'
                )
            )
        data.append(scatter)

    figure = go.Figure(
        data=data,
        layout=layout
    )
    return figure

In [34]:
layout = go.Layout(
            margin=dict(l=0, r=0, b=0, t=0),
            scene=dict(
                xaxis=dict(
                    title='Component 1',
                    showgrid=True,
                    zeroline=False,
                    showticklabels=True
                ),
                yaxis=dict(
                    title='Component 2',
                    showgrid=True,
                    zeroline=False,
                    showticklabels=True
                ),
                zaxis=dict(
                    title='Component 3',
                    showgrid=True,
                    zeroline=False,
                    showticklabels=True
                )
            )
        )

In [35]:
pop_resolution = 'label'

df_dim = reduce_dim(X, algorithm='PCA')
df_dim = pd.concat([df_dim, label],1)
groups = df_dim.groupby(pop_resolution)
figure = generate_figure_image(groups, layout)
iplot(figure)

In [20]:
pop_resolution = 'label'

df_dim = reduce_dim(X, algorithm='UMAP')
df_dim = pd.concat([df_dim, label],1)
groups = df_dim.groupby(pop_resolution)
figure = generate_figure_image(groups, layout)
iplot(figure)

In [21]:
pop_resolution = 'label'

df_dim = reduce_dim(X, algorithm='TSNE')
df_dim = pd.concat([df_dim, label],1)
groups = df_dim.groupby(pop_resolution)
figure = generate_figure_image(groups, layout)
iplot(figure)

In [22]:
# Now we will create a class to enable plotting radar charts
import plotly.graph_objects as go
import plotly.offline as pyo
import plotly.express as px
from plotly.subplots import make_subplots


# We will create a class to polar plots because we are going to apply the same settings
# for multiple charts. By creating a class we can standardize that and change configs in only one place.
class PolarPlot():

    def __init__(self, title):
        pyo.init_notebook_mode() # allows plotly to show charts on notebook 
        self.figure = go.Figure() # instatiates plotly figure
        self.range = (0, 0) # define the initial range of polar plots
        self.title = title # Saves the chart title as an attribute
        self.theta = ['Business Analyst', 'Data Analyst', 'Data Scientist', 'Data Engineer/DBA',
                      'Software Engineer', 'Statistician/Research Scientist', 'Business Analyst'] # Those are the Theta values for our plot
    
    def update_common_layout(self):
        """
        Updates general layout characteristics
        """
        self.figure.update_layout(
            showlegend = True,
            title_text = self.title, # add title to chart from attribute
            title_font_color = '#333333', # Grey is always better to not draw much attention
            title_font_size = 14,
            legend_font_color = 'grey', # We don't want to draw attention to the legend 
            legend_itemclick = 'toggleothers', # Change the default behaviour, when click select only that trace
            legend_itemdoubleclick = 'toggle', # Change the default behaviour, when double click ommit that trace
            width = 800, # chart size 
            height = 500 # chart size
        )
        
    def update_commom_polar_layout(self):
        """
        Updates polar layout characteristics
        """
        self.figure.update_layout(
            polar_bgcolor='white', # White background is always better
            polar_radialaxis_visible=True, # we want to show the axis
            polar_radialaxis_showticklabels=True, # we want to show the axis titles
            polar_radialaxis_tickfont_color='darkgrey', # grey to the axis label (Software Engineer, Data Scientist, etc)
            polar_angularaxis_color='grey', # Always grey for all elements that are not important
            polar_angularaxis_showline=False, # hide lines that are not necessary
            polar_radialaxis_showline=False, # hide lines that are not necessary
            polar_radialaxis_layer='below traces', # show the axis bellow all traces
            polar_radialaxis_gridcolor='#F2F2F2', # grey to not draw attention
            polar_radialaxis_range=self.range # gets the range attribute, that is calculated in another method
        )
        
    def add_data(self, data, country, color, hover_template='%{r:0.0f}%'):
        """
        Adds a trace to the figure following the same standard for each trace
        """
        highlight = color != 'lightslategrey' # We only want to highlight a few traces, this will decide if a trace is highlighted or not
        data.append(data[0]) # add the first element to the end of the list, this will "close" the polar chart 
        self.figure.add_trace(
            go.Scatterpolar(
                r=data, # Data points 
                theta=self.theta, # Axis (Software Engineer, Data Scientist, etc)
                mode='lines', # plot mode to lines (not good to show markers, it usually adds cluttering to chart)
                name=country, # name to be exibited on legend and on hover
                hoverinfo='name+r', # what to show on hover (name + data point)
                hovertemplate=hover_template, # Format of data point
                line_color=color, # line color
                showlegend=highlight, # will decide if show or not the legend, only shows if color != lightslategrey. Otherwise we would have one legend for each trace. Too much clutter.
                opacity= 0.8 if highlight else 0.25, # If we want to highlight, then oppacity is 0.8. Otherwise it is 0.25, to reduce clutter.
                line_shape='spline', # This will allow smoothing the lines
                line_smoothing=0.8, # How much the lines will smooth
                line_width=1.6 if highlight else 0.6 # we want highlighted traces to be more evident, otherwise they should stay in the background 
            )
        )
        self.update_range(data) # Calls the method that will update the max range
    
    def update_range(self, data):
        """
        Updates the range to be 110% of maximum value of all traces
        """
        max_range = max(data) * 1.1
        self.range = (0, max_range) if max_range > self.range[1] else self.range # updates the range attribute
        
    def show(self):
        """
        Update layouts and shows the figure
        """
        self.update_common_layout() 
        self.update_commom_polar_layout()
        self.figure.show()

In [23]:
# as we have many charts displaying job titles per country, we will create anoter class to handle this
class JobTitlebyCountry:
    
    def __init__(self, country_color, polar_plot):
        self.countries = list(set(kaggle.Country.tolist())) # defines the list of countries as all countries available on Kaggle dataset
        self.country_color = country_color # It is a dictionary of country names and colors
        self.polar = polar_plot # PolarPlot() instance that we have defined before
        
        for country in self.country_color.keys():
            # Here we remove countries that will be highlighted and add then back to the end of the list
            # this way we avoid having non highlighted traces over them
            self.countries.remove(country)
            self.countries.append(country)
    
    def add_traces_percentage(self, data):
        """
        Calculates the percentage of rows for each job title in each country and then add it to plot
        """
        for country in self.countries:
            # iterates in the list of countries
            data_filtered = data[data.Country == country] # filters data for a single country
            if len(data_filtered) > 20: # only plotting if there are more than 20 datapoints
                color = self.country_color.get(country, 'lightslategrey') # check if country is in the dict of countries and get color, if it is not then color is lightslategrey
                plot_data = data_filtered.groupby(['JobTitle'], as_index=False).Count.sum().Count.tolist() # group the data by jobtitle, perform count and convert it to a list 
                plot_data = (np.array(plot_data) / sum(plot_data) * 100).tolist() # Transform absolute values into percentages
                self.polar.add_data(plot_data, country, color) # add trace to the figure
    
    def add_traces_average_salary(self, data):
        """
        Calculates the average salary for each job title in each country and then add it to plot
        """
        for country in self.countries:
            data_filtered = data[data.Country == country]
            if len(data_filtered) > 20: # only plotting if there are more than 20 datapoints
                color = self.country_color.get(country, 'lightslategrey')
                plot_data = data_filtered.groupby(['JobTitle'], as_index=False).Salary.mean() # Group by job title and calculate average salary
                plot_data.dropna(inplace=True) # drop all nulls
                plot_data = plot_data.Salary.tolist()
                if len(plot_data) == 6: #removes countries that dont have salary for all job titles
                    self.polar.add_data(plot_data, country, color, 'U$%{r:,.2r}') # add trace to figure
          
    def adjust_layout_percentage(self):
        """
        Adjust layout to show percentages
        """
        self.polar.figure.update_layout(
            polar_radialaxis_tickvals=[25, 50, 75], # show ticks ate 25, 50 and 75
            polar_radialaxis_ticktext=['25%', '50%', '75%'],
            polar_radialaxis_tickmode='array',
        )